# Sujet 7 : Autour du SARS-CoV-2 (Covid-19)


## Consignes :

### Prérequis

Techniques de présentation graphique. Cet exercice peut être réalisé indifféremment en R ou en Python.

### Sujet

Le but est ici de reproduire des graphes semblables à ceux du South China Morning Post (SCMP), sur la page The Coronavirus Pandemic et qui montrent pour différents pays le nombre cumulé (c'est-à-dire le nombre total de cas depuis le début de l'épidémie) de personnes atteintes de la maladie à coronavirus 2019.

Les données que nous utiliserons dans un premier temps sont compilées par le Johns Hopkins University Center for Systems Science and Engineering (JHU CSSE) et sont mises à disposition sur GitHub. C'est plus particulièrement sur les données time_series_covid19_confirmed_global.csv (des suites chronologiques au format csv) disponibles à l'adresse : https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_confirmed_global.csv, que nous allons nous concentrer.

Vous commencerez par télécharger les données pour créer un graphe montrant l’évolution du nombre de cas cumulé au cours du temps pour les pays suivants : la Belgique (Belgium), la Chine - toutes les provinces sauf Hong-Kong (China), Hong Kong (China, Hong-Kong), la France métropolitaine (France), l’Allemagne (Germany), l’Iran (Iran), l’Italie (Italy), le Japon (Japan), la Corée du Sud (Korea, South), la Hollande sans les colonies (Netherlands), le Portugal (Portugal), l’Espagne (Spain), le Royaume-Unis sans les colonies (United Kingdom), les États-Unis (US).

Le nom entre parenthèses est le nom du « pays » tel qu’il apparaît dans le fichier time_series_covid19_confirmed_global.csv. Les données de la Chine apparaissent par province et nous avons séparé Hong-Kong, non pour prendre parti dans les différences entre cette province et l'état chinois, mais parce que c'est ainsi qu'apparaissent les données sur le site du SCMP. Les données pour la France, la Hollande et le Royaume-Uni excluent les territoires d'outre-mer et autres « résidus coloniaux ».

Ensuite vous ferez un graphe avec la date en abscisse et le nombre cumulé de cas à cette date en ordonnée. Nous vous proposons de faire deux versions de ce graphe, une avec une échelle linéaire et une avec une échelle logarithmique.

### Question subsidiaire à faire quand on sera sorti du « merdier »

Vous pourrez également utiliser les données de décès (timeseriescovid19deathsglobal.csv) et refaire les courbes, mais là encore, faites attention lors de l'interprétation. Ces courbes, même si elles paraissent effrayantes, doivent être comparées à la mortalité « normale ». Pour la France des données sont disponibles sur le site de l'INSEE : https://www.insee.fr/fr/information/4470857, ainsi que dans les « Points hebdomadaires » de surveillance de la mortalité diffusés par Santé publique France, comme celui de la semaine 12 (le site étant très mal conçu pour quiconque souhaite une information spécifique, le plus simple est de passer par un moteur de recherche généraliste…).

Pour atténuer les effets dus aux méthodes de comptage, etc., vous pourrez, une fois l'épidémie terminée, prendre les données du nombre total de décès et les normaliser pour 1000 habitants du pays concerné. Vous irez ensuite chercher les données sur le nombre de lits d'hôpital pour 1000 habitants sur le site de l'OCDE et vous pourrez corréler les deux (c'est-à-dire, faire un graphe avec le nombre de lits en abscisse et le nombre de décès en ordonnée)…

---

# Pour commencer

Nous allons tout d'abord importer les outils necéssaires pour réaliser ce travail.



In [1]:
%matplotlib inline

import os
import urllib.request

import matplotlib.pyplot as plt
import pandas as pd
import isoweek

Nous pouvons maintenant télécharger les [données](https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_confirmed_global.csv) si elles ne sont pas déjà téléchargés.

In [2]:
# URL des données
data_url = "https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_confirmed_global.csv"

# Nom du fichier csv
data_file = "data_covid.csv"

# Téléchargement des données si elles ne sont pas déjà présentes dans le répertoire
if not os.path.exists(data_file):
    urllib.request.urlretrieve(data_url, data_file)

# Affichage des données
raw_data = pd.read_csv(data_file)
raw_data

Province/State          Country/Region  \
0                                             NaN             Afghanistan   
1                                             NaN                 Albania   
2                                             NaN                 Algeria   
3                                             NaN                 Andorra   
4                                             NaN                  Angola   
5                                             NaN     Antigua and Barbuda   
6                                             NaN               Argentina   
7                                             NaN                 Armenia   
8                    Australian Capital Territory               Australia   
9                                 New South Wales               Australia   
10                             Northern Territory               Australia   
11                                     Queensland               Australia   
12                                South Australia               Australia   
13                                       Tasmania               Australia   
14                                       Victoria               Australia   
15                              Western Australia               Australia   
16                                            NaN                 Austria   
17                                            NaN              Azerbaijan   
18                                            NaN                 Bahamas   
19                                            NaN                 Bahrain   
20                                            NaN              Bangladesh   
21                                            NaN                Barbados   
22                                            NaN                 Belarus   
23                                            NaN                 Belgium   
24                                            NaN                  Belize   
25                                            NaN                   Benin   
26                                            NaN                  Bhutan   
27                                            NaN                 Bolivia   
28                                            NaN  Bosnia and Herzegovina   
29                                            NaN                Botswana   
..                                            ...                     ...   
244                                           NaN             Timor-Leste   
245                                           NaN                    Togo   
246                                           NaN     Trinidad and Tobago   
247                                           NaN                 Tunisia   
248                                           NaN                  Turkey   
249                                           NaN                      US   
250                                           NaN                  Uganda   
251                                           NaN                 Ukraine   
252                                           NaN    United Arab Emirates   
253                                      Anguilla          United Kingdom   
254                                       Bermuda          United Kingdom   
255                        British Virgin Islands          United Kingdom   
256                                Cayman Islands          United Kingdom   
257                               Channel Islands          United Kingdom   
258                   Falkland Islands (Malvinas)          United Kingdom   
259                                     Gibraltar          United Kingdom   
260                                   Isle of Man          United Kingdom   
261                                    Montserrat          United Kingdom   
262  Saint Helena, Ascension and Tristan da Cunha          United Kingdom   
263                      Turks and Caicos Islands          United Kingdom   
264                            

Ces données sont organisés sur 274 lignes pour chaque pays et (pour le moment) 412 colonnes présentant la province, le pays, les latitudes et longitudes suivi du nombre de cas par jour du 22 Janvier 2020 au 4 Mars 2021 au moment de l'écriture de ce rapport.

Filtrons les données en choisant les colonnes des dates la regex `\d{1,2}\/\d{1,2}\/\d{2}` sélectionne les colonnes dont le nom commence par :
un ou deux chiffres suivi d'un "/", deux fois, puis se terminent par deux chiffres
c'est à dire les colonnes des dates (vous pouvez inverser la regex avec `[^\d{1,2}\/\d{1,2}\/\d{2}]` pour constater que la commande fait bien l'inverse et nous rend des données avec des NaN)

In [3]:
raw_data[raw_data.filter(regex="\d{1,2}\/\d{1,2}\/\d{2}").isnull().any(axis=1)]

Empty DataFrame
Columns: [Province/State, Country/Region, Lat, Long, 1/22/20, 1/23/20, 1/24/20, 1/25/20, 1/26/20, 1/27/20, 1/28/20, 1/29/20, 1/30/20, 1/31/20, 2/1/20, 2/2/20, 2/3/20, 2/4/20, 2/5/20, 2/6/20, 2/7/20, 2/8/20, 2/9/20, 2/10/20, 2/11/20, 2/12/20, 2/13/20, 2/14/20, 2/15/20, 2/16/20, 2/17/20, 2/18/20, 2/19/20, 2/20/20, 2/21/20, 2/22/20, 2/23/20, 2/24/20, 2/25/20, 2/26/20, 2/27/20, 2/28/20, 2/29/20, 3/1/20, 3/2/20, 3/3/20, 3/4/20, 3/5/20, 3/6/20, 3/7/20, 3/8/20, 3/9/20, 3/10/20, 3/11/20, 3/12/20, 3/13/20, 3/14/20, 3/15/20, 3/16/20, 3/17/20, 3/18/20, 3/19/20, 3/20/20, 3/21/20, 3/22/20, 3/23/20, 3/24/20, 3/25/20, 3/26/20, 3/27/20, 3/28/20, 3/29/20, 3/30/20, 3/31/20, 4/1/20, 4/2/20, 4/3/20, 4/4/20, 4/5/20, 4/6/20, 4/7/20, 4/8/20, 4/9/20, 4/10/20, 4/11/20, 4/12/20, 4/13/20, 4/14/20, 4/15/20, 4/16/20, 4/17/20, 4/18/20, 4/19/20, 4/20/20, 4/21/20, 4/22/20, 4/23/20, 4/24/20, 4/25/20, 4/26/20, ...]
Index: []

[0 rows x 412 columns]

Le tableau en sortie est bien vide, il ne manque donc aucune donnée importante.

Listons les pays que nous allons analyser, ils sont tous représentés dans les données par le nom du pays dans la colonne `Country/Region` et `Nan` dans la colonne `Province/State` sauf dans le cas de la Chine ou nous allons devoir faire une somme de toutes les provinces d'un coté et de récupérer Hong-Knog de l'autre.

In [12]:
countries = [ 
        "Belgium",
        "France",
        "Germany",
        "Iran",
        "Italy",
        "Japan",
        "Korea, South",
        "Netherlands",
        "Portugal",
        "Spain",
        "United Kingdom",
        "US",
#         "China",
#         "China, Hong-Kong",
]

Enregistrons les lignes consernées dans un nouveau tableau :

In [28]:
data = []
for country in countries:
    new_row = raw_data[(raw_data['Country/Region']==country) & (raw_data['Province/State'].isnull())].values.tolist()
    print(new_row)
dataf = pd.DataFrame(data, columns=raw_data.columns)

[[nan, 'France', 46.2276, 2.2137, 0, 0, 2, 3, 3, 3, 4, 5, 5, 5, 6, 6, 6, 6, 6, 6, 6, 11, 11, 11, 11, 11, 11, 11, 12, 12, 12, 12, 12, 12, 12, 12, 12, 12, 14, 18, 38, 57, 100, 130, 191, 212, 285, 423, 613, 938, 1115, 1401, 1773, 2281, 2281, 3661, 4469, 4499, 6633, 7652, 9043, 10871, 12612, 14282, 16533, 19856, 22054, 24967, 28856, 32609, 37162, 39761, 44029, 51579, 56362, 58404, 63588, 46483, 47299, 49934, 46400, 50242, 54003, 55538, 56972, 107712, 110836, 128272, 131476, 144035, 145896, 149683, 150752, 153197, 155821, 157603, 155881, 158653, 160295, 160907, 164592, 167650, 166193, 167326, 167846, 168637, 168887, 169405, 170467, 174596, 175218, 175743, 176132, 176338, 176651, 177330, 177790, 178353, 178837, 179140, 179250, 179650, 180143, 180499, 180752, 181444, 181969, 181410, 181684, 181880, 182018, 185300, 185842, 187608, 187817, 187986, 187265, 184015, 188286, 188808, 189330, 189621, 189782, 190266, 190743, 191040, 191679, 192043, 192317, 192369, 192915, 193256, 193576, 194121, 19453

In [29]:
dataf

Empty DataFrame
Columns: [Province/State, Country/Region, Lat, Long, 1/22/20, 1/23/20, 1/24/20, 1/25/20, 1/26/20, 1/27/20, 1/28/20, 1/29/20, 1/30/20, 1/31/20, 2/1/20, 2/2/20, 2/3/20, 2/4/20, 2/5/20, 2/6/20, 2/7/20, 2/8/20, 2/9/20, 2/10/20, 2/11/20, 2/12/20, 2/13/20, 2/14/20, 2/15/20, 2/16/20, 2/17/20, 2/18/20, 2/19/20, 2/20/20, 2/21/20, 2/22/20, 2/23/20, 2/24/20, 2/25/20, 2/26/20, 2/27/20, 2/28/20, 2/29/20, 3/1/20, 3/2/20, 3/3/20, 3/4/20, 3/5/20, 3/6/20, 3/7/20, 3/8/20, 3/9/20, 3/10/20, 3/11/20, 3/12/20, 3/13/20, 3/14/20, 3/15/20, 3/16/20, 3/17/20, 3/18/20, 3/19/20, 3/20/20, 3/21/20, 3/22/20, 3/23/20, 3/24/20, 3/25/20, 3/26/20, 3/27/20, 3/28/20, 3/29/20, 3/30/20, 3/31/20, 4/1/20, 4/2/20, 4/3/20, 4/4/20, 4/5/20, 4/6/20, 4/7/20, 4/8/20, 4/9/20, 4/10/20, 4/11/20, 4/12/20, 4/13/20, 4/14/20, 4/15/20, 4/16/20, 4/17/20, 4/18/20, 4/19/20, 4/20/20, 4/21/20, 4/22/20, 4/23/20, 4/24/20, 4/25/20, 4/26/20, ...]
Index: []

[0 rows x 412 columns]